In [1]:
import pandas as pd, numpy as np, dataprep as dp
import torch
import matplotlib.pyplot as plt

In [2]:
df = pd.read_csv("/Users/florian/Documents/github/study/IoT/IoT/aggregated_hourly.csv")
a0 = ["hka-aqm-a017", "hka-aqm-a014"]
a1 = ["hka-aqm-a101", "hka-aqm-a102", "hka-aqm-a103", "hka-aqm-a106", "hka-aqm-a107", "hka-aqm-a108", "hka-aqm-a111", "hka-aqm-a112"]

In [25]:
px.scatter(df, x="date_time", y= "tmp", color= "device_id").show()

In [3]:
df_cutoff = df.copy
df_cutoff = dp.cutoff_data(df, "2023-01-13", "2023-03-28")
df_mean = dp.build_lvl_df(df_cutoff, a1, ["tmp", "hum", "CO2"], reset_ind= True)
df_mean.head()

tmp     hum    CO2
0  23.0950  34.000  573.0
1  23.1125  33.840  545.0
2  23.0950  33.865  532.0
3  23.1650  33.825  516.0
4  23.2725  33.780  507.0

In [21]:
import plotly.express as px

px.line(df_mean, x=df_mean.index, y="hum", title="Temperature")

In [5]:
X = df_mean.to_numpy()
y = df_mean["tmp"].shift(-1).to_numpy()
X.shape, y.shape

((1775, 3), (1775,))

In [6]:
X_train, X_test, y_train, y_test = dp.train_test_split(X, y)
X_train.shape, y_train.shape, X_test.shape, y_test.shape

(torch.Size([1748, 3]),
 torch.Size([1748]),
 torch.Size([27, 3]),
 torch.Size([27]))

In [7]:
X_train_new, X_test_new = dp.format_tensor(X_train), dp.format_tensor(X_test)
X_train = X_train_new
X_test = X_test_new
y_train = y_train[:-1]#.unsqueeze(1)
y_test = y_test[:-1]#.unsqueeze(1)
X_train.shape, X_test.shape, y_train.shape, y_test.shape

(torch.Size([1747, 48, 3]),
 torch.Size([26, 48, 3]),
 torch.Size([1747]),
 torch.Size([26]))

In [8]:
from torch.utils.data import DataLoader, TensorDataset

batch_size = 64

train_data = TensorDataset(X_train, y_train)
test_data = TensorDataset(X_test, y_test)

train_loader = DataLoader(train_data, shuffle=True, batch_size=batch_size)
test_loader = DataLoader(test_data, shuffle=False, batch_size=batch_size)

In [9]:
from foo import LSTM

LSTM_model = LSTM(input_size=X_train.shape[2], hidden_size=100, num_layers=1, output_size=1)

In [10]:
from torch.optim import lr_scheduler 

num_epochs = 50
learning_rate = 0.001
criterion = torch.nn.MSELoss()
optimizer = torch.optim.Adam(LSTM_model.parameters(), lr=learning_rate)
scheduler = lr_scheduler.ExponentialLR(optimizer, gamma= 0.99)

LSTM_model.train()
#labels = []
#outputs = []
for epoch in range(num_epochs):
    for i, (features, target) in enumerate(train_loader):
        optimizer.zero_grad(set_to_none=True)
        output = LSTM_model(features)
        target = target.unsqueeze(1)
        loss = criterion(output, target)
        loss.backward()
        optimizer.step()
        #labels.extend(target.detach().numpy()[0])
        #outputs.extend(output.detach().numpy()[0])
        if (i+1) % 10 == 0:
            print('Epoch [{}/{}], Step [{}/{}], Loss: {:.4f}'.format(epoch+1, num_epochs, i+1, len(train_loader), loss.item()))
    scheduler.step()
print(scheduler.get_last_lr())

Epoch [1/50], Step [10/28], Loss: 413.0391
Epoch [1/50], Step [20/28], Loss: 397.8299
Epoch [2/50], Step [10/28], Loss: 341.0675
Epoch [2/50], Step [20/28], Loss: 327.3229
Epoch [3/50], Step [10/28], Loss: 307.0235
Epoch [3/50], Step [20/28], Loss: 291.0348
Epoch [4/50], Step [10/28], Loss: 268.0323
Epoch [4/50], Step [20/28], Loss: 257.4341
Epoch [5/50], Step [10/28], Loss: 228.5105
Epoch [5/50], Step [20/28], Loss: 213.7316
Epoch [6/50], Step [10/28], Loss: 195.1823
Epoch [6/50], Step [20/28], Loss: 173.9093
Epoch [7/50], Step [10/28], Loss: 152.2995
Epoch [7/50], Step [20/28], Loss: 148.2865
Epoch [8/50], Step [10/28], Loss: 133.3786
Epoch [8/50], Step [20/28], Loss: 119.4037
Epoch [9/50], Step [10/28], Loss: 110.1398
Epoch [9/50], Step [20/28], Loss: 100.3771
Epoch [10/50], Step [10/28], Loss: 92.3859
Epoch [10/50], Step [20/28], Loss: 83.8992
Epoch [11/50], Step [10/28], Loss: 71.0399
Epoch [11/50], Step [20/28], Loss: 69.3053
Epoch [12/50], Step [10/28], Loss: 65.6800
Epoch [12/5

In [11]:
LSTM_model.eval()  # Set the model to evaluation mode

test_features, test_targets = next(iter(test_loader))  # Get a batch of test data
test_targets = test_targets.unsqueeze(1)  # Expand target to match the output shape
test_targets[-1] = 21.0213

with torch.no_grad():  # Disable gradient computation
    predictions = LSTM_model(test_features)  # Make predictions

# Calculate the mean squared error of the predictions
test_loss = criterion(predictions, test_targets)
print('Test Loss: {:.4f}'.format(test_loss.item()))

Test Loss: 1.8170


In [12]:
test_targets

tensor([[20.9122],
        [20.8471],
        [20.8037],
        [20.9935],
        [20.9821],
        [20.9251],
        [20.8888],
        [20.8687],
        [20.9183],
        [20.6574],
        [21.4696],
        [22.5116],
        [22.6053],
        [22.5800],
        [22.5087],
        [22.4242],
        [22.4840],
        [22.5582],
        [22.5919],
        [22.5121],
        [22.1749],
        [21.9574],
        [21.7229],
        [21.4908],
        [21.2156],
        [21.0213]])

In [13]:
import plotly.graph_objects as go

def plt_pred(test_targets, predictions):
    fig = go.Figure()
    fig.add_trace(go.Scatter(y=test_targets, mode='lines', name='test_targets'))
    fig.add_trace(go.Scatter(y=predictions, mode='lines', name='Predictions'))
    fig.update_layout(title='test_targets vs predictions', xaxis_title='Index', yaxis_title='Value')
    fig.show()

plt_pred(test_targets.view(-1).tolist(), predictions.view(-1).tolist())

In [14]:
torch.save(LSTM_model.state_dict(), "LSTM_model.pth")